First of all, we set up a function to parse all the input, and a data class.

In [50]:
import java.io.File

data class Operation(var amount: Int, var action: Action) {
    enum class Action { ADD, MULTIPLY, SQUARE }
}
data class Monkey(var items:MutableList<Int>,
    var operation: Operation,
    var divisor: Int,
    var trueTarget: Int,
    var falseTarget: Int)

fun read(file: String): MutableList<Monkey> {
    val monkeys: MutableList<Monkey> = mutableListOf()
    var items: MutableList<Int> = mutableListOf()
    var operation: Operation = Operation(0, Operation.Action.ADD)
    var divisor = 0
    var trueTarget = 0
    var falseTarget = 0

    for (line in File(file).readLines()) {
        if (line.contains("Starting items:")) {
            items = line.substringAfter(":").split(",").map { Integer.parseInt(it.trim()) }.toMutableList();
        }

        if (line.contains("Operation")) {
            val op = when (line.substringAfter("old ")[0]) {
                '*' -> Operation.Action.MULTIPLY
                '+' -> Operation.Action.ADD
                else -> Operation.Action.ADD
            }
            if (line.substringAfter("old").contains("old")) {
                operation = Operation(0, Operation.Action.SQUARE)
            } else {
                val amt = Integer.parseInt(line.substringAfter("old ").substring(1).trim())
                operation = Operation(amt, op)
            }
        }

        if (line.contains("Test:")) {
            divisor = Integer.parseInt(line.substringAfter("divisible by "))
        }
        if (line.contains("If true:")) {
            trueTarget = Integer.parseInt(line.substringAfter("monkey "))
        }
        if (line.contains("If false:")) {
            falseTarget = Integer.parseInt(line.substringAfter("monkey "))
        }

        if (line.isBlank()) {
            monkeys.add(Monkey(items, operation, divisor, trueTarget, falseTarget))
        }
    }

    
    return monkeys
}

Next up we need a function for executing one step of all the monkeys' actions.

In [51]:
fun operate(op: Operation, x: Int): Int {
    return when (op.action) {
        Operation.Action.ADD -> x + op.amount
        Operation.Action.MULTIPLY -> x * op.amount
        Operation.Action.SQUARE -> x * x
    } / 3
}
fun execute(monkeys: MutableList<Monkey>, idx: Int): Int {
    val me = monkeys[idx]
    for (i in 0..<me.items.count()) {
        val worry = operate(me.operation, me.items[i])
        if (worry % me.divisor == 0) monkeys[me.trueTarget].items.add(worry)
        else monkeys[me.falseTarget].items.add(worry)
    }
    val output = me.items.count()
    me.items.clear()
    return output
}

fun runRound(monkeys: MutableList<Monkey>, monkeyBusiness: MutableList<Int>) {
    for (i in 0..<monkeys.count()) {
        monkeyBusiness[i] += execute(monkeys, i);
    }
}

Now that we've set everything up, it's time to fly!

In [58]:
val monkeys = read("b.input")
var monkeyBusiness = monkeys.map { 0 } .toMutableList()

println("$monkeys")

for (i in 0..100) {
    //println("After round ${i+1}:")
    runRound(monkeys, monkeyBusiness)
    println("${monkeyBusiness.sortedDescending().take(2).reduce{a,b->a*b}}")
}


[Monkey(items=[71, 86], operation=Operation(amount=13, action=MULTIPLY), divisor=19, trueTarget=6, falseTarget=7), Monkey(items=[66, 50, 90, 53, 88, 85], operation=Operation(amount=3, action=ADD), divisor=2, trueTarget=5, falseTarget=4), Monkey(items=[97, 54, 89, 62, 84, 80, 63], operation=Operation(amount=6, action=ADD), divisor=13, trueTarget=4, falseTarget=1), Monkey(items=[82, 97, 56, 92], operation=Operation(amount=2, action=ADD), divisor=5, trueTarget=6, falseTarget=0), Monkey(items=[50, 99, 67, 61, 86], operation=Operation(amount=0, action=SQUARE), divisor=7, trueTarget=5, falseTarget=3), Monkey(items=[61, 66, 72, 55, 64, 53, 72, 63], operation=Operation(amount=4, action=ADD), divisor=11, trueTarget=3, falseTarget=0), Monkey(items=[59, 79, 63], operation=Operation(amount=7, action=MULTIPLY), divisor=17, trueTarget=2, falseTarget=7), Monkey(items=[55], operation=Operation(amount=7, action=ADD), divisor=3, trueTarget=2, falseTarget=1)]
108
304
957
1974
3074
4891
6880
8930
12760
15

In [43]:
296*298

88208